# KDD 2009 - Tratamento de dados simplista
Como parte do exercício de resolução do KDD Cup de 2009 criamos este notebook para realizar um teste do modelo preditivo sem fazer grandes alterações nos dados originais.

Os únicos tratamentos dos dados de entrada serão:
- Remoção das variáveis nulas (sem nenhum valor válido)
- Conversão das variáveis categóricas para valores numéricos

In [1]:
# Importação de bibliotecas
import math
import matplotlib as mpl
import numpy as np
import os
import pandas as pd
import random
from sklearn.metrics import auc
import sys
import xgboost as xgb

# Rotinas de visualização de dados
from bokeh.plotting import figure
from bokeh.io import output_notebook, push_notebook, show, export_png
from bokeh.models import Range1d

output_notebook()

Loading BokehJS ...

# Lendo arquivo de treinamento

Arquivo possui 50000 entradas, arquivos de labels (churn, appetency, upselling) em separado

In [2]:
# Diretório de dados
data_folder = os.path.join("..", "data")
# Arquivo de dados
training_data_file = os.path.join(data_folder, "orange_small_train.data")

# Dataframae com os dados de treinamento
kdd2009 = pd.read_csv(training_data_file, delimiter='\t', na_values=[''])


## Limpeza dos dados
Verificar se há colunas de dados apenas com NaNs, remove estas colunas, caso existam.

In [3]:
# Número total de pontos de dados
numeroDados = len(kdd2009)

# Cria dataframe com contagem de NaNs
nans = pd.DataFrame(kdd2009.isna().sum(), columns=['NAN_count'])
# Recupera lista de variaveis que só possuem NaN
variaveisNulas = nans[nans['NAN_count'] == numeroDados].index.values

# Remove as colunas que só contém NaNs
kdd2009.drop(variaveisNulas, axis=1, inplace=True)

# Lendo arquivos de labels
Lendo arquivos com os rótulos de *Appetency, Churn* e *Upselling*, que estão em arquivos separados. Os labels serão incluídos no dataframe do kdd2009

In [4]:
# Arquivos com os rótulos das métricas
# Colunas de resultados
resultados = ['appetency', 'churn', 'upselling']
padraoArquivosRotulos = "orange_small_train_{}.labels"

# Colunas de variáveis de entrada
variaveis = kdd2009.keys()

# Le os arquivos de rótulos, converte 1 -> True, -1 -> False e inclui no dataframe do kdd
for rotulo in resultados:
    # Gera nome do arquivo
    nomeArquivo = os.path.join(data_folder, padraoArquivosRotulos.format(rotulo))
    # Lê arquivo
    dfRotulo = pd.read_csv(nomeArquivo, header=None, names=['label'])
    # Converte 1 -> True, -1 -> False - Assume que != 1 -> False
    dfRotulo['label'] = dfRotulo['label'] == 1
    # Inclusão dos rótulos no dataframe do kdd como colunas adicionais
    kdd2009[rotulo] = dfRotulo['label']

# Verificando os rótulos no DataFrame

In [5]:
# Primeiros valores dos resultados no dataframe de treinamento
kdd2009[resultados].head()

appetency  churn  upselling
0      False  False      False
1      False   True      False
2      False  False      False
3      False  False      False
4      False  False      False

## E verificando as variáveis (já sem colunas de NaNs)

In [6]:
# Primeiros valores das variaveis no dataframe de treinamento
kdd2009[variaveis].head()

Var1  Var2  Var3  Var4  Var5    Var6  Var7  Var9  Var10  Var11  ...  \
0   NaN   NaN   NaN   NaN   NaN  1526.0   7.0   NaN    NaN    NaN  ...   
1   NaN   NaN   NaN   NaN   NaN   525.0   0.0   NaN    NaN    NaN  ...   
2   NaN   NaN   NaN   NaN   NaN  5236.0   7.0   NaN    NaN    NaN  ...   
3   NaN   NaN   NaN   NaN   NaN     NaN   0.0   NaN    NaN    NaN  ...   
4   NaN   NaN   NaN   NaN   NaN  1029.0   7.0   NaN    NaN    NaN  ...   

    Var220   Var221   Var222      Var223  Var224  Var225  Var226   Var227  \
0  1YVfGrO     oslk  fXVEsaq  jySVZNlOJy     NaN     NaN    xb3V     RAYp   
1  0AJo2f2     oslk  2Kb5FSF  LM8l689qOp     NaN     NaN    fKCe     RAYp   
2  JFM1BiF  Al6ZaUT  NKv4yOc  jySVZNlOJy     NaN    kG3k    Qu4f  02N6s8f   
3  L91KIiz     oslk  CE7uk3u  LM8l689qOp     NaN     NaN    FSa2     RAYp   
4  OrnLfvc     oslk  1J2cvxe  LM8l689qOp     NaN    kG3k    FSa2     RAYp   

          Var228  Var229  
0  F2FyR07IdsN7I     NaN  
1  F2FyR07IdsN7I     NaN  
2  ib5G6X1eUxUn6    am7c  
3  F2FyR07IdsN7I     NaN  
4  F2FyR07IdsN7I    mj86  

[5 rows x 212 columns]

# Conversão de colunas de objetos e booleanos para inteiros
Classifica as colunas em inteiros, reais, objetos e booleanos e depois converte objetos e booleans para inteiros. O algoritmo que será utilizado para treinamento requer que os dados sejam inteiros ou reais.

In [7]:
# Verifica os tipos de dados existentes no dataframe
print('Lista de tipos de dados no kdd2009: {}'.format(list(set(kdd2009[variaveis].dtypes))))

Lista de tipos de dados no kdd2009: [dtype('O'), dtype('float64'), dtype('int64')]


In [8]:
data_types = pd.DataFrame(kdd2009[variaveis].dtypes, columns=['dtype'])

variaveisInteiras = list(data_types[data_types.values == np.dtype('int64')].index.values)
variaveisReais = list(data_types[data_types.values == np.dtype('float64')].index.values)
variaveisCategoricas = list(data_types[data_types.values == np.dtype('object')].index.values)

len(variaveisInteiras+variaveisReais+variaveisCategoricas+resultados) == len(kdd2009.keys())

print('Há {} variáveis inteiras, {} variáveis reais e {} objetos'.format(
                                                                    len(variaveisInteiras),
                                                                    len(variaveisReais),
                                                                    len(variaveisCategoricas)))

# Verifica se o total de tipos de variáveis está correto
if len(variaveisInteiras+variaveisReais+variaveisCategoricas+resultados) != len(kdd2009.keys()):
    print('Aviso: erro na contagem de tipos de variáveis!!!')

Há 1 variáveis inteiras, 173 variáveis reais e 38 objetos


## As variáveis categóricas serão convertidas em inteiros
Não seria necessário converter os booleanos para inteiros, já que Python 3 representa True como 1 e False como 0

In [9]:
kdd2009[variaveisCategoricas].head()

Var191      Var192   Var193 Var194 Var195 Var196 Var197   Var198  \
0    NaN  bZkvyxLkBI     RO12    NaN   taul   1K8T   lK27  ka_ns41   
1    NaN  CEat0G8rTN     RO12    NaN   taul   1K8T   2Ix5  qEdASpP   
2    NaN  eOQt0GoOh3  AERks4l   SEuy   taul   1K8T   ffXs  NldASpP   
3    NaN  jg69tYsGvO     RO12    NaN   taul   1K8T   ssAy  _ybO0dd   
4    NaN  IXSgUHShse     RO12   SEuy   taul   1K8T   uNkU  EKR938I   

          Var199   Var200  ...   Var220   Var221   Var222      Var223 Var224  \
0     nQUveAzAF7      NaN  ...  1YVfGrO     oslk  fXVEsaq  jySVZNlOJy    NaN   
1     y2LIM01bE1      NaN  ...  0AJo2f2     oslk  2Kb5FSF  LM8l689qOp    NaN   
2        y4g9XoZ  vynJTq9  ...  JFM1BiF  Al6ZaUT  NKv4yOc  jySVZNlOJy    NaN   
3  4hMlgkf58mhwh      NaN  ...  L91KIiz     oslk  CE7uk3u  LM8l689qOp    NaN   
4        ThrHXVS  0v21jmy  ...  OrnLfvc     oslk  1J2cvxe  LM8l689qOp    NaN   

  Var225 Var226   Var227         Var228 Var229  
0    NaN   xb3V     RAYp  F2FyR07IdsN7I    NaN  
1    NaN   fKCe     RAYp  F2FyR07IdsN7I    NaN  
2   kG3k   Qu4f  02N6s8f  ib5G6X1eUxUn6   am7c  
3    NaN   FSa2     RAYp  F2FyR07IdsN7I    NaN  
4   kG3k   FSa2     RAYp  F2FyR07IdsN7I   mj86  

[5 rows x 38 columns]

In [10]:
kdd2009.describe()

Var1         Var2           Var3         Var4          Var5  \
count  702.000000  1241.000000    1240.000000  1579.000000  1.487000e+03   
mean    11.487179     0.004029     425.298387     0.125396  2.387933e+05   
std     40.709951     0.141933    4270.193518     1.275481  6.441259e+05   
min      0.000000     0.000000       0.000000     0.000000  0.000000e+00   
25%      0.000000     0.000000       0.000000     0.000000  0.000000e+00   
50%      0.000000     0.000000       0.000000     0.000000  0.000000e+00   
75%     16.000000     0.000000       0.000000     0.000000  1.187425e+05   
max    680.000000     5.000000  130668.000000    27.000000  6.048550e+06   

                Var6          Var7         Var9         Var10        Var11  \
count   44471.000000  44461.000000   702.000000  1.487000e+03  1240.000000   
mean     1326.437116      6.809496    48.145299  3.926057e+05     8.625806   
std      2685.693668      6.326053   154.777855  9.280896e+05     2.869558   
min         0.000000      0.000000     0.000000  0.000000e+00     8.000000   
25%       518.000000      0.000000     4.000000  0.000000e+00     8.000000   
50%       861.000000      7.000000    20.000000  0.000000e+00     8.000000   
75%      1428.000000      7.000000    46.000000  2.628630e+05     8.000000   
max    131761.000000    140.000000  2300.000000  1.232559e+07    40.000000   

       ...        Var180        Var181        Var182        Var183  \
count  ...  7.020000e+02  44991.000000  1.579000e+03  1.241000e+03   
mean   ...  3.776755e+06      0.611456  1.416638e+06  7.777380e+04   
std    ...  3.785696e+06      2.495681  2.279786e+06  2.016188e+05   
min    ...  0.000000e+00      0.000000  0.000000e+00  0.000000e+00   
25%    ...  1.917352e+05      0.000000  0.000000e+00  0.000000e+00   
50%    ...  2.431310e+06      0.000000  1.167780e+05  0.000000e+00   
75%    ...  6.471827e+06      0.000000  1.844952e+06  4.881000e+04   
max    ...  1.428483e+07     49.000000  1.199478e+07  3.048400e+06   

            Var184      Var186     Var187       Var188        Var189  \
count  1241.000000  702.000000  702.00000  1241.000000  21022.000000   
mean      8.460919    3.299145   16.54416   167.368477    270.142137   
std      46.973777    8.781967   60.22303   113.980072     86.707692   
min       0.000000    0.000000    0.00000    -6.420000      6.000000   
25%       0.000000    0.000000    0.00000    19.380000    204.000000   
50%       0.000000    0.000000    4.00000   197.640000    270.000000   
75%       8.000000    6.000000   14.00000   252.960000    330.000000   
max    1200.000000  102.000000  910.00000   628.620000    642.000000   

              Var190  
count     333.000000  
mean    22007.045192  
std     29085.146490  
min         0.000000  
25%      2732.670000  
50%     12668.940000  
75%     29396.340000  
max    230427.000000  

[8 rows x 174 columns]

In [11]:
kdd2009.head()

Var1  Var2  Var3  Var4  Var5    Var6  Var7  Var9  Var10  Var11  ...  \
0   NaN   NaN   NaN   NaN   NaN  1526.0   7.0   NaN    NaN    NaN  ...   
1   NaN   NaN   NaN   NaN   NaN   525.0   0.0   NaN    NaN    NaN  ...   
2   NaN   NaN   NaN   NaN   NaN  5236.0   7.0   NaN    NaN    NaN  ...   
3   NaN   NaN   NaN   NaN   NaN     NaN   0.0   NaN    NaN    NaN  ...   
4   NaN   NaN   NaN   NaN   NaN  1029.0   7.0   NaN    NaN    NaN  ...   

       Var223  Var224  Var225  Var226   Var227         Var228  Var229  \
0  jySVZNlOJy     NaN     NaN    xb3V     RAYp  F2FyR07IdsN7I     NaN   
1  LM8l689qOp     NaN     NaN    fKCe     RAYp  F2FyR07IdsN7I     NaN   
2  jySVZNlOJy     NaN    kG3k    Qu4f  02N6s8f  ib5G6X1eUxUn6    am7c   
3  LM8l689qOp     NaN     NaN    FSa2     RAYp  F2FyR07IdsN7I     NaN   
4  LM8l689qOp     NaN    kG3k    FSa2     RAYp  F2FyR07IdsN7I    mj86   

   appetency  churn  upselling  
0      False  False      False  
1      False   True      False  
2      False  False      False  
3      False  False      False  
4      False  False      False  

[5 rows x 215 columns]

## Convertendo variáveis categóricas para inteiros (para usar no XGBoost)

In [12]:
for variavel in variaveisCategoricas:
    kdd2009[variavel] = pd.Categorical(kdd2009[variavel])
    kdd2009[variavel] = kdd2009[variavel].cat.codes

In [13]:
# Verifica os tipos de dados existentes no dataframe
print('Lista de tipos de dados no kdd2009: {}'.format(list(set(kdd2009[variaveis].dtypes))))

Lista de tipos de dados no kdd2009: [dtype('float64'), dtype('int64'), dtype('int16'), dtype('int8')]


In [14]:
kdd2009.head()

Var1  Var2  Var3  Var4  Var5    Var6  Var7  Var9  Var10  Var11  ...  \
0   NaN   NaN   NaN   NaN   NaN  1526.0   7.0   NaN    NaN    NaN  ...   
1   NaN   NaN   NaN   NaN   NaN   525.0   0.0   NaN    NaN    NaN  ...   
2   NaN   NaN   NaN   NaN   NaN  5236.0   7.0   NaN    NaN    NaN  ...   
3   NaN   NaN   NaN   NaN   NaN     NaN   0.0   NaN    NaN    NaN  ...   
4   NaN   NaN   NaN   NaN   NaN  1029.0   7.0   NaN    NaN    NaN  ...   

   Var223  Var224  Var225  Var226  Var227  Var228  Var229  appetency  churn  \
0       3      -1      -1      22       2       8      -1      False  False   
1       0      -1      -1      14       2       8      -1      False   True   
2       3      -1       1      10       0      25       0      False  False   
3       0      -1      -1       7       2       8      -1      False  False   
4       0      -1       1       7       2       8       1      False  False   

   upselling  
0      False  
1      False  
2      False  
3      False  
4      False  

[5 rows x 215 columns]

In [15]:
kdd2009.describe()

Var1         Var2           Var3         Var4          Var5  \
count  702.000000  1241.000000    1240.000000  1579.000000  1.487000e+03   
mean    11.487179     0.004029     425.298387     0.125396  2.387933e+05   
std     40.709951     0.141933    4270.193518     1.275481  6.441259e+05   
min      0.000000     0.000000       0.000000     0.000000  0.000000e+00   
25%      0.000000     0.000000       0.000000     0.000000  0.000000e+00   
50%      0.000000     0.000000       0.000000     0.000000  0.000000e+00   
75%     16.000000     0.000000       0.000000     0.000000  1.187425e+05   
max    680.000000     5.000000  130668.000000    27.000000  6.048550e+06   

                Var6          Var7         Var9         Var10        Var11  \
count   44471.000000  44461.000000   702.000000  1.487000e+03  1240.000000   
mean     1326.437116      6.809496    48.145299  3.926057e+05     8.625806   
std      2685.693668      6.326053   154.777855  9.280896e+05     2.869558   
min         0.000000      0.000000     0.000000  0.000000e+00     8.000000   
25%       518.000000      0.000000     4.000000  0.000000e+00     8.000000   
50%       861.000000      7.000000    20.000000  0.000000e+00     8.000000   
75%      1428.000000      7.000000    46.000000  2.628630e+05     8.000000   
max    131761.000000    140.000000  2300.000000  1.232559e+07    40.000000   

       ...       Var220        Var221        Var222        Var223  \
count  ...  50000.00000  50000.000000  50000.000000  50000.000000   
mean   ...   2003.12184      3.984080   2123.702060      0.302480   
std    ...   1248.04682      1.119166   1183.541455      1.070238   
min    ...      0.00000      0.000000      0.000000     -1.000000   
25%    ...    826.00000      4.000000   1066.000000      0.000000   
50%    ...   2014.00000      4.000000   2230.000000      0.000000   
75%    ...   3047.00000      4.000000   2984.250000      0.000000   
max    ...   4290.00000      6.000000   4290.000000      3.000000   

             Var224        Var225        Var226        Var227        Var228  \
count  50000.000000  50000.000000  50000.000000  50000.000000  50000.000000   
mean      -0.983600     -0.220100     10.115720      2.103060     10.233400   
std        0.127009      0.933506      5.798438      0.867994      6.488254   
min       -1.000000     -1.000000      0.000000      0.000000      0.000000   
25%       -1.000000     -1.000000      6.000000      2.000000      8.000000   
50%       -1.000000     -1.000000     10.000000      2.000000      8.000000   
75%       -1.000000      1.000000     14.000000      2.000000      8.000000   
max        0.000000      2.000000     22.000000      6.000000     29.000000   

             Var229  
count  50000.000000  
mean      -0.368800  
std        0.799074  
min       -1.000000  
25%       -1.000000  
50%       -1.000000  
75%        0.000000  
max        3.000000  

[8 rows x 212 columns]

# Divisão do conjunto de dados em treinamento, validação e verificação cruzada
Os dados originais serão divididos em tres conjunto:

- Treinamento, com 90% dos dados (45.000 dados)
- Validação, com 5% dos dados (2.500 dados)
- Verificação cruzada, com 5% dos dados (2.500 dados)

In [16]:
# Fixa semente para reproduzir resultados
random.seed(42)

# Define treino como 90% dos dados de treino e
# validação como os 10% restantes
tamanhoTreino = math.floor(0.9 * numeroDados)

# Gera uma amostra aleatória com parte dos índices
indicesTreino = random.sample(range(numeroDados), tamanhoTreino)
indicesValidacaoVC = list(set(range(numeroDados)) - set(indicesTreino))
metade = len(indicesValidacaoVC)//2
indicesValidacao = indicesValidacaoVC[:metade]
indicesVC = indicesValidacaoVC[metade:]

# Divide os dados nos dois subgrupos
# -indicesTreino são os 10% dos índices restantes
dadosTreino = kdd2009.iloc[indicesTreino].reset_index(drop=True)
dadosValidacao = kdd2009.iloc[indicesValidacao].reset_index(drop=True)
dadosVCruzada = kdd2009.iloc[indicesVC].reset_index(drop=True)

# Dimensões dos dados de treino e validação
print("Dados de treinamento: {}, Dados de validação: {}".format(len(dadosTreino), len(dadosValidacao)))

Dados de treinamento: 45000, Dados de validação: 2500


## Verificando os dataframes

In [17]:
dadosTreino.head()

Var1  Var2  Var3  Var4  Var5    Var6  Var7  Var9  Var10  Var11  ...  \
0   NaN   NaN   NaN   NaN   NaN   392.0   0.0   NaN    NaN    NaN  ...   
1   NaN   NaN   NaN   NaN   NaN  1911.0   0.0   NaN    NaN    NaN  ...   
2   NaN   NaN   NaN   NaN   NaN   854.0   7.0   NaN    NaN    NaN  ...   
3   NaN   NaN   NaN   NaN   NaN  2331.0   7.0   NaN    NaN    NaN  ...   
4   NaN   NaN   NaN   NaN   NaN   119.0   0.0   NaN    NaN    NaN  ...   

   Var223  Var224  Var225  Var226  Var227  Var228  Var229  appetency  churn  \
0      -1      -1      -1       8       2       8      -1      False  False   
1       0      -1      -1      14       2       8      -1      False  False   
2       0      -1       1      12       1       2       0       True  False   
3       0      -1       0      17       4       8       0      False  False   
4      -1      -1      -1       1       0       8      -1      False  False   

   upselling  
0      False  
1      False  
2      False  
3      False  
4      False  

[5 rows x 215 columns]

In [18]:
dadosValidacao.head()

Var1  Var2  Var3  Var4  Var5    Var6  Var7  Var9  Var10  Var11  ...  \
0   NaN   NaN   NaN   NaN   NaN  1204.0   0.0   NaN    NaN    NaN  ...   
1   NaN   NaN   NaN   NaN   NaN   805.0   7.0   NaN    NaN    NaN  ...   
2   NaN   NaN   NaN   NaN   NaN   539.0   7.0   NaN    NaN    NaN  ...   
3   NaN   NaN   NaN   NaN   NaN  1155.0  14.0   NaN    NaN    NaN  ...   
4   NaN   NaN   NaN   NaN   NaN   693.0   7.0   NaN    NaN    NaN  ...   

   Var223  Var224  Var225  Var226  Var227  Var228  Var229  appetency  churn  \
0       0      -1      -1      16       2       8      -1      False  False   
1       0      -1       0       9       2       8       0      False  False   
2       0      -1      -1      18       2       8      -1      False   True   
3       3      -1       1       4       2       2       0      False  False   
4       0      -1      -1       7       2       8      -1      False  False   

   upselling  
0      False  
1      False  
2      False  
3      False  
4      False  

[5 rows x 215 columns]

In [19]:
dadosVCruzada.head()

Var1  Var2  Var3  Var4  Var5    Var6  Var7  Var9  Var10  Var11  ...  \
0   NaN   NaN   NaN   NaN   NaN    63.0   0.0   NaN    NaN    NaN  ...   
1   NaN   NaN   NaN   NaN   NaN  1344.0   7.0   NaN    NaN    NaN  ...   
2   NaN   NaN   NaN   NaN   NaN   308.0   7.0   NaN    NaN    NaN  ...   
3   NaN   NaN   NaN   NaN   NaN   840.0   7.0   NaN    NaN    NaN  ...   
4   NaN   NaN   NaN   NaN   NaN   126.0   0.0   NaN    NaN    NaN  ...   

   Var223  Var224  Var225  Var226  Var227  Var228  Var229  appetency  churn  \
0       0      -1      -1      11       2       8      -1      False  False   
1       0      -1      -1       0       2       8       0      False  False   
2       0      -1       2       4       2       8       1      False  False   
3       0      -1      -1      12       2       8      -1      False  False   
4       0      -1      -1       6       2       8      -1      False  False   

   upselling  
0      False  
1      False  
2      False  
3      False  
4      False  

[5 rows x 215 columns]

## Verificando a distribuição dos rótulos entre treino, validação e referência cruzada

In [20]:
dadosTreino[resultados].sum()

appetency     805
churn        3341
upselling    3327
dtype: int64

In [21]:
dadosValidacao[resultados].sum()

appetency     37
churn        159
upselling    164
dtype: int64

In [22]:
dadosVCruzada[resultados].sum()

appetency     48
churn        172
upselling    191
dtype: int64

# XGBoost

Utilizaremos o [XGBoost](https://xgboost.readthedocs.io/en/latest/index.html) para treinamento dos dados do KDD2009 e predição de resultados no conjunto de testes

In [23]:
# Variável que será prevista
resultado = 'upselling'

### Rotinas de chamada do XGBoost
- gradeBoost: Recebe dados de treinamento, de teste, o rótulo a ser testado e um iterador para a grade de treinamento
- xgBoost: Rotina que chama o XGBoost com os parâmetros desejados

In [24]:
def gradeBoost(treinamento, listaVariaveis, teste, rotulo, intervaloGrade, verbose=0):
    """ Gera lista de resultados da grade de treinamento.
    Parâmetros:
    treinamento: Dataframe de dados de treinamento, com variaveis e rotulos
    listaVariaveis: Lista de variáveis para treinamento/teste
    teste: Dataframe de dados de teste/validação
    rotulo: Rotulo do teste
    intervaloGrade: Range de intervalo da grade de treinamento
    """
    # TODO: Tratamento de parâmetros/datarames de entrada
    
    # Converte dataframes para DMatrices
    xgbDados = xgb.DMatrix(treinamento[listaVariaveis], treinamento[[rotulo]])
    xgbTeste = xgb.DMatrix(teste[listaVariaveis])
    
    # Converte rotulos booleanos para inteiro (embora não seja estritamente necessário em python)
    validacao = teste[rotulo].apply(int).reset_index(drop=True)

    # Vetor de resultados
    resultados = []
    for rodada in intervaloGrade:
        resultados.append(xgBoost(xgbDados, xgbTeste, validacao, rotulo, rodada, verbose=verbose))
    dfResultado = pd.DataFrame()
    return resultados

def xgBoost(treinamento, teste, validacao, rotulo, rodadas, verbose=0):
    """ Executa o xgBoost e retorna tupla com número de rodadas e AUC
    """
    param = {'booster': 'dart',
             #'objective': 'binary:logistic',
             #'eta': 0.05,
             #'gamma': 0,
             'max_depth': 7,
             #'min_child_weight': 1,
             #'subsample': 1,
             #'colsample_bytree': 1
            }
    if verbose:
        print('XGBoost, {rodadas} rodadas'.format(rodadas=rodadas))
    # Treina modelo pelo número de rodadas determinado
    modelo = xgb.train(param, treinamento, rodadas)
    
    # Computa a previsão do modelo para o conjunto de teste
    resultadoValidacao = modelo.predict(teste)

    # Cria dataframe com previsão e rótulo
    previsao = 'previsao'
    dfPrevisao = pd.DataFrame(resultadoValidacao, columns=[previsao])
    dfPrevisao[rotulo] = validacao
    
    # Ordena o dataframe pela coluna de previsao
    dfPrevisao = dfPrevisao.sort_values(by=previsao)
    # Usamos o AUC do sklearn.metrics
    # requer: from sklearn.metrics import auc
    aucRun = auc(dfPrevisao[previsao], dfPrevisao[rotulo])
    if verbose:
        print('----------> AUC: {}'.format(aucRun))
    return (rodadas, aucRun)
    

# Visualização de resultados

In [25]:
# Rotinas para geração de gráficos
def linha(dados, x="x", y="y", fig=None, delay=False, **kwargs):
    p = figure(width=900, height=600) if fig == None else fig
    p.y_range = Range1d(0,1)
    p.line(x, y, source=dados, **kwargs)
    if delay == False:
        show(p)
    return p
    
def linhaAUC(dados, fig=None, delay=False, **kwargs):
    return linha(dados, "Rodadas", "AUC", fig=fig, delay=delay, **kwargs)

In [26]:
iteracoes = range(5, 150, 1)

In [27]:
grade = gradeBoost(dadosTreino, variaveis, dadosValidacao, resultado, iteracoes, verbose=1)

XGBoost, 5 rodadas
[17:17:12] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 172 extra nodes, 0 pruned nodes, max_depth=7
[17:17:12] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:12] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 164 extra nodes, 0 pruned nodes, max_depth=7
[17:17:12] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:13] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 168 extra nodes, 0 pruned nodes, max_depth=7
[17:17:13] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:13] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 176 extra nodes, 0 pruned nodes, max_depth=7
[17:17:13] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:13] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 188 extra nodes, 0 pruned nodes, max_depth=7
[17:17:13] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
---------->

[17:17:20] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 164 extra nodes, 0 pruned nodes, max_depth=7
[17:17:20] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:20] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 152 extra nodes, 0 pruned nodes, max_depth=7
[17:17:20] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:21] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 180 extra nodes, 0 pruned nodes, max_depth=7
[17:17:21] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:21] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 166 extra nodes, 0 pruned nodes, max_depth=7
[17:17:21] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
----------> AUC: 0.42686519026756287
XGBoost, 11 rodadas
[17:17:21] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 172 extra nodes, 0 pruned nodes, max_depth=7
[17:17:21] /workspace/src/gbm/gbtree.cc:492

[17:17:28] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 168 extra nodes, 0 pruned nodes, max_depth=7
[17:17:28] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:29] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 176 extra nodes, 0 pruned nodes, max_depth=7
[17:17:29] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:29] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 188 extra nodes, 0 pruned nodes, max_depth=7
[17:17:29] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:29] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 180 extra nodes, 0 pruned nodes, max_depth=7
[17:17:29] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:29] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 164 extra nodes, 0 pruned nodes, max_depth=7
[17:17:29] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:30] /workspace/src/tree

[17:17:37] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 172 extra nodes, 0 pruned nodes, max_depth=7
[17:17:37] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:37] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 164 extra nodes, 0 pruned nodes, max_depth=7
[17:17:37] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:37] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 168 extra nodes, 0 pruned nodes, max_depth=7
[17:17:37] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:37] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 176 extra nodes, 0 pruned nodes, max_depth=7
[17:17:37] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:38] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 188 extra nodes, 0 pruned nodes, max_depth=7
[17:17:38] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:38] /workspace/src/tree

[17:17:45] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 152 extra nodes, 0 pruned nodes, max_depth=7
[17:17:45] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:46] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 180 extra nodes, 0 pruned nodes, max_depth=7
[17:17:46] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:46] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 166 extra nodes, 0 pruned nodes, max_depth=7
[17:17:46] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:46] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 140 extra nodes, 0 pruned nodes, max_depth=7
[17:17:46] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:46] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 146 extra nodes, 0 pruned nodes, max_depth=7
[17:17:46] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[17:17:46] /workspace/src/tree

...

[18:03:54] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 138 extra nodes, 0 pruned nodes, max_depth=7
[18:03:54] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:03:54] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 106 extra nodes, 0 pruned nodes, max_depth=7
[18:03:54] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:03:54] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 104 extra nodes, 0 pruned nodes, max_depth=7
[18:03:54] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:03:55] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 164 extra nodes, 0 pruned nodes, max_depth=7
[18:03:55] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:03:55] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 136 extra nodes, 0 pruned nodes, max_depth=7
[18:03:55] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:03:55] /workspace/src/tree

[18:04:08] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 176 extra nodes, 0 pruned nodes, max_depth=7
[18:04:08] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:08] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 152 extra nodes, 0 pruned nodes, max_depth=7
[18:04:08] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:08] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 168 extra nodes, 0 pruned nodes, max_depth=7
[18:04:08] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:09] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 162 extra nodes, 0 pruned nodes, max_depth=7
[18:04:09] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:09] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 116 extra nodes, 0 pruned nodes, max_depth=7
[18:04:09] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:10] /workspace/src/tree

[18:04:19] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 156 extra nodes, 0 pruned nodes, max_depth=7
[18:04:19] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:20] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 106 extra nodes, 0 pruned nodes, max_depth=7
[18:04:20] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:20] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 160 extra nodes, 0 pruned nodes, max_depth=7
[18:04:20] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:20] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 128 extra nodes, 0 pruned nodes, max_depth=7
[18:04:20] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:21] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 142 extra nodes, 0 pruned nodes, max_depth=7
[18:04:21] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:21] /workspace/src/tree

[18:04:30] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 154 extra nodes, 0 pruned nodes, max_depth=7
[18:04:30] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:30] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 188 extra nodes, 0 pruned nodes, max_depth=7
[18:04:30] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:31] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 92 extra nodes, 0 pruned nodes, max_depth=7
[18:04:31] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:31] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 116 extra nodes, 0 pruned nodes, max_depth=7
[18:04:31] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:31] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 110 extra nodes, 0 pruned nodes, max_depth=7
[18:04:31] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:32] /workspace/src/tree/

[18:04:43] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 138 extra nodes, 0 pruned nodes, max_depth=7
[18:04:43] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:43] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 116 extra nodes, 0 pruned nodes, max_depth=7
[18:04:43] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:44] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 114 extra nodes, 0 pruned nodes, max_depth=7
[18:04:44] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:44] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 176 extra nodes, 0 pruned nodes, max_depth=7
[18:04:44] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:44] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 156 extra nodes, 0 pruned nodes, max_depth=7
[18:04:44] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:45] /workspace/src/tree

In [28]:
grade

[(5, 0.3242570161819458),
 (6, 0.3729969710111618),
 (7, 0.4032677412033081),
 (8, 0.4375940412282944),
 (9, 0.4237157106399536),
 (10, 0.42686519026756287),
 (11, 0.43934205174446106),
 (12, 0.41491489112377167),
 (13, 0.46997812390327454),
 (14, 0.4837155193090439),
 (15, 0.4806153029203415),
 (16, 0.48095984756946564),
 (17, 0.4843840003013611),
 (18, 0.4695894867181778),
 (19, 0.4638829082250595),
 (20, 0.5007139891386032),
 (21, 0.4834529459476471),
 (22, 0.5370551943778992),
 (23, 0.5565512776374817),
 (24, 0.5694490969181061),
 (25, 0.5804675817489624),
 (26, 0.5736615657806396),
 (27, 0.568538174033165),
 (28, 0.5769093185663223),
 (29, 0.5590820461511612),
 (30, 0.5174060314893723),
 (31, 0.525955080986023),
 (32, 0.525559812784195),
 (33, 0.516302302479744),
 (34, 0.5380240380764008),
 (35, 0.5335802137851715),
 (36, 0.539239227771759),
 (37, 0.5443762838840485),
 (38, 0.5493879914283752),
 (39, 0.5493541210889816),
 (40, 0.5572347790002823),
 (41, 0.5680517107248306),
 (42, 

In [29]:
dfGrade = pd.DataFrame({"AUC":[g[1] for g in grade], "Rodadas":[g[0] for g in grade]})

In [30]:
aucMax = dfGrade["AUC"].max()
numRodadas = dfGrade[dfGrade["AUC"] == aucMax]["Rodadas"].iloc[0]
print('AUC Máximo: {}, {} rodadas'.format(aucMax, numRodadas))

AUC Máximo: 0.6959377080202103, 119 rodadas


In [31]:
fig = linhaAUC(dfGrade, color="red", legend="Teste")

## Resultado da Validação Cruzada
A medida AUC desejada é dada pela Validação Cruzada, com dados que não fizeram parte do treinamento e validação do modelo

In [32]:
resultadoVCruzada = gradeBoost(dadosTreino, variaveis, dadosVCruzada, resultado, (numRodadas,), verbose=1)

XGBoost, 119 rodadas
[18:04:59] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 172 extra nodes, 0 pruned nodes, max_depth=7
[18:04:59] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:59] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 164 extra nodes, 0 pruned nodes, max_depth=7
[18:04:59] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:59] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 168 extra nodes, 0 pruned nodes, max_depth=7
[18:04:59] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:04:59] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 176 extra nodes, 0 pruned nodes, max_depth=7
[18:04:59] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:00] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 188 extra nodes, 0 pruned nodes, max_depth=7
[18:05:00] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:00

[18:05:09] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 118 extra nodes, 0 pruned nodes, max_depth=7
[18:05:09] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:10] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 102 extra nodes, 0 pruned nodes, max_depth=7
[18:05:10] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:10] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 148 extra nodes, 0 pruned nodes, max_depth=7
[18:05:10] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:10] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 102 extra nodes, 0 pruned nodes, max_depth=7
[18:05:10] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:10] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 102 extra nodes, 0 pruned nodes, max_depth=7
[18:05:10] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:11] /workspace/src/tree

[18:05:21] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 104 extra nodes, 0 pruned nodes, max_depth=7
[18:05:21] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:22] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 164 extra nodes, 0 pruned nodes, max_depth=7
[18:05:22] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:22] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 136 extra nodes, 0 pruned nodes, max_depth=7
[18:05:22] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:22] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 108 extra nodes, 0 pruned nodes, max_depth=7
[18:05:22] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:22] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 142 extra nodes, 0 pruned nodes, max_depth=7
[18:05:22] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:23] /workspace/src/tree

In [33]:
print(resultadoVCruzada)

[(119, 0.5778907686471939)]


# Comparação de comportamento entre Testes e Validação Cruzada

Para ter uma ideia mais clara da previsibilidade do modelo, vamos comparar os resultados globais dos dados de Testes (e não apenas o melhor resultado) com os resultados com os dados de Validação Cruzada 

In [34]:
gradeVCruzada = gradeBoost(dadosTreino, variaveis, dadosVCruzada, resultado, iteracoes, verbose=1)

XGBoost, 5 rodadas
[18:05:31] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 172 extra nodes, 0 pruned nodes, max_depth=7
[18:05:31] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:32] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 164 extra nodes, 0 pruned nodes, max_depth=7
[18:05:32] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:32] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 168 extra nodes, 0 pruned nodes, max_depth=7
[18:05:32] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:32] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 176 extra nodes, 0 pruned nodes, max_depth=7
[18:05:32] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:33] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 188 extra nodes, 0 pruned nodes, max_depth=7
[18:05:33] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
---------->

[18:05:40] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 164 extra nodes, 0 pruned nodes, max_depth=7
[18:05:40] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:40] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 152 extra nodes, 0 pruned nodes, max_depth=7
[18:05:40] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:40] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 180 extra nodes, 0 pruned nodes, max_depth=7
[18:05:40] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:40] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 166 extra nodes, 0 pruned nodes, max_depth=7
[18:05:40] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
----------> AUC: 0.5256420224905014
XGBoost, 11 rodadas
[18:05:41] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 172 extra nodes, 0 pruned nodes, max_depth=7
[18:05:41] /workspace/src/gbm/gbtree.cc:492:

[18:05:49] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 176 extra nodes, 0 pruned nodes, max_depth=7
[18:05:49] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:49] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 188 extra nodes, 0 pruned nodes, max_depth=7
[18:05:49] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:49] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 180 extra nodes, 0 pruned nodes, max_depth=7
[18:05:49] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:49] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 164 extra nodes, 0 pruned nodes, max_depth=7
[18:05:49] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:49] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 152 extra nodes, 0 pruned nodes, max_depth=7
[18:05:49] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:49] /workspace/src/tree

[18:05:58] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 172 extra nodes, 0 pruned nodes, max_depth=7
[18:05:58] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:58] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 164 extra nodes, 0 pruned nodes, max_depth=7
[18:05:58] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:58] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 168 extra nodes, 0 pruned nodes, max_depth=7
[18:05:58] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:58] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 176 extra nodes, 0 pruned nodes, max_depth=7
[18:05:58] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:58] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 188 extra nodes, 0 pruned nodes, max_depth=7
[18:05:58] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:05:59] /workspace/src/tree

[18:06:06] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 152 extra nodes, 0 pruned nodes, max_depth=7
[18:06:06] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:06:06] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 180 extra nodes, 0 pruned nodes, max_depth=7
[18:06:06] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:06:06] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 166 extra nodes, 0 pruned nodes, max_depth=7
[18:06:06] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:06:06] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 140 extra nodes, 0 pruned nodes, max_depth=7
[18:06:06] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:06:06] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 146 extra nodes, 0 pruned nodes, max_depth=7
[18:06:06] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:06:07] /workspace/src/tree

...

[18:53:00] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 136 extra nodes, 0 pruned nodes, max_depth=7
[18:53:00] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:00] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 108 extra nodes, 0 pruned nodes, max_depth=7
[18:53:00] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:01] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 142 extra nodes, 0 pruned nodes, max_depth=7
[18:53:01] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:01] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 92 extra nodes, 0 pruned nodes, max_depth=7
[18:53:01] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:01] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 146 extra nodes, 0 pruned nodes, max_depth=7
[18:53:01] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:02] /workspace/src/tree/

[18:53:15] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 116 extra nodes, 0 pruned nodes, max_depth=7
[18:53:15] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:16] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 72 extra nodes, 0 pruned nodes, max_depth=7
[18:53:16] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:16] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 202 extra nodes, 0 pruned nodes, max_depth=7
[18:53:16] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:16] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 80 extra nodes, 0 pruned nodes, max_depth=7
[18:53:16] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:17] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 160 extra nodes, 0 pruned nodes, max_depth=7
[18:53:17] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:17] /workspace/src/tree/u

[18:53:27] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 142 extra nodes, 0 pruned nodes, max_depth=7
[18:53:27] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:27] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 84 extra nodes, 0 pruned nodes, max_depth=7
[18:53:27] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:27] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 106 extra nodes, 0 pruned nodes, max_depth=7
[18:53:27] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:27] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 134 extra nodes, 0 pruned nodes, max_depth=7
[18:53:27] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:28] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 136 extra nodes, 0 pruned nodes, max_depth=7
[18:53:28] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:28] /workspace/src/tree/

[18:53:37] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 110 extra nodes, 0 pruned nodes, max_depth=7
[18:53:37] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:38] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 110 extra nodes, 0 pruned nodes, max_depth=7
[18:53:38] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:38] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 152 extra nodes, 0 pruned nodes, max_depth=7
[18:53:38] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:38] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 134 extra nodes, 0 pruned nodes, max_depth=7
[18:53:38] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:39] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 110 extra nodes, 0 pruned nodes, max_depth=7
[18:53:39] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:39] /workspace/src/tree

[18:53:50] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 156 extra nodes, 0 pruned nodes, max_depth=7
[18:53:50] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:51] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 118 extra nodes, 0 pruned nodes, max_depth=7
[18:53:51] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:51] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 194 extra nodes, 0 pruned nodes, max_depth=7
[18:53:51] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:52] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 166 extra nodes, 0 pruned nodes, max_depth=7
[18:53:52] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:52] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 118 extra nodes, 0 pruned nodes, max_depth=7
[18:53:52] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:53:52] /workspace/src/tree

In [35]:
gradeVCruzada

[(5, 0.41871246695518494),
 (6, 0.4492481052875519),
 (7, 0.5095944404602051),
 (8, 0.5301965624094009),
 (9, 0.5272092968225479),
 (10, 0.5256420224905014),
 (11, 0.5262809097766876),
 (12, 0.5017445683479309),
 (13, 0.5134692192077637),
 (14, 0.5114529430866241),
 (15, 0.5070465207099915),
 (16, 0.5159243494272232),
 (17, 0.5323897153139114),
 (18, 0.514386847615242),
 (19, 0.5131175071001053),
 (20, 0.5191761702299118),
 (21, 0.5042760819196701),
 (22, 0.51075878739357),
 (23, 0.5394548326730728),
 (24, 0.5451803505420685),
 (25, 0.5348891317844391),
 (26, 0.5152008086442947),
 (27, 0.5113163739442825),
 (28, 0.526541531085968),
 (29, 0.5279685854911804),
 (30, 0.5242465436458588),
 (31, 0.5194537937641144),
 (32, 0.5161419361829758),
 (33, 0.5252111554145813),
 (34, 0.5305970013141632),
 (35, 0.531652495265007),
 (36, 0.514760747551918),
 (37, 0.4987971633672714),
 (38, 0.5012199282646179),
 (39, 0.4903210550546646),
 (40, 0.48192283511161804),
 (41, 0.469428688287735),
 (42, 0.476

In [36]:
dfGradeVCruzada = pd.DataFrame({"AUC":[g[1] for g in gradeVCruzada], "Rodadas":[g[0] for g in gradeVCruzada]})

In [37]:
fig = linhaAUC(dfGradeVCruzada, fig=fig, legend="Validação Cruzada")

In [38]:
arquivoSaida = os.path.join('imagens', 'xgBoost_AUC_{rotulo}.png'.format(rotulo=resultado))
export_png(fig, filename=arquivoSaida)

'/media/stelling/OS/xampp/htdocs/KDD2009/python/imagens/xgBoost_AUC_upselling.png'

[](file:///media/stelling/OS/xampp/htdocs/KDD2009/python/imagens/xgBoost_AUC_churn.png')

# AUC/Rodada
![nada](imagens/xgBoost_AUC_upselling.png)

# Conclusão

